# INM433 Visual Analytics: Lab05

## Coursework Planning Workshop

### Objective

Investigate some of the effects of lockdown on use of the London Bike Hire Scheme.

### Data

TFL's daily number of bike hires data

How many bikes are at each bike station at 10-minute intervals since the scheme started

### Research Questions

### Suggested Approach

#### Libraries

In [1]:
import pandas as pd
import altair as alt
from pyproj import Transformer

### Dataset 1: Daily Number of Bike Hires

#### Load the Data

In [2]:
dailyHires = pd.read_excel('tfl-daily-cycle-hires.xlsx', sheet_name='Data')

# just take the first two columns (usage by day) (the other columns aggregate by month or year - open in Excel to have a look)
dailyHires = dailyHires.iloc[:,[0,1]]

dailyHires.head()

Day  Number of Bicycle Hires
0 2010-07-30                     6897
1 2010-07-31                     5564
2 2010-08-01                     4303
3 2010-08-02                     6642
4 2010-08-03                     7966

#### Compare 2020 with the Rest

Refer to https://altair-viz.github.io/user_guide/transform/timeunit.html for variations of time unit transformation.

In [3]:
# Save the whole chart (all years) as in a variable.
allYears = alt.Chart(dailyHires).mark_line().encode(
    x = 'month(Day):T',
    y = 'sum(Number of Bicycle Hires):Q',
    color = "year(Day):O"
)

# Save the whole just for 2020 as in a variable.
# The 2020 data is filtered out using Panda (first line)
just2020 = alt.Chart(dailyHires[dailyHires.Day.dt.year == 2020]).mark_line().encode(
    x = 'month(Day):T',
    y = 'sum(Number of Bicycle Hires):Q',
    color = alt.value("firebrick")
)

# Superimpose both graphs
allYears + just2020

alt.LayerChart(...)

#### Compare 2019 and 2020 by Month

In [4]:
# Filter on the 2 years
dailyHires2019_2020 = dailyHires[(dailyHires.Day.dt.year == 2019)|(dailyHires.Day.dt.year == 2020)]

alt.Chart(dailyHires2019_2020).mark_line().encode(
    x='date(Day):T',
    y='sum(Number of Bicycle Hires):Q',
    color='year(Day):N',
    column='month(Day):T',
    tooltip='Day:T'
).properties(
    width=100,
    height=100
)

alt.Chart(...)

##### Comments
- The decrease in the last 2 weeks of March 2021 is due to the first lockdown.
- The spikes in in 2021 after April is because people stopped going to offices, so usage in weekdays has been decreased while the usage in weekends has been increased since people cycled instead of using public transportation.

##### Further Computations
Weekly temporal dstribution to understand how week days and weekends are compared.

### Dataset 2: Station Status in every 10 Minutes

#### Load the Data

1 week periods from 2019 and 2020:
- 2019, March 25 and 31 (2019-03-25 and 2019-03-31)
- 2020, March 23 and 29 (2020-03-23 and 2020-03-29)

In [5]:
# Load the 2019 data
tenMinStationBikes = pd.read_csv('week2019.csv')

# Append the 2020 data
tenMinStationBikes=tenMinStationBikes.append(pd.read_csv('week2020.csv'))

# Convert to date format
tenMinStationBikes['t']=pd.to_datetime(tenMinStationBikes['t'])

# Derive a year column
tenMinStationBikes['year']=tenMinStationBikes['t'].dt.year

In [6]:
# Display
tenMinStationBikes.head()

stationId  availableBikes  availableDocks                   t  year
0          1              14               5 2019-03-25 00:00:02  2019
1          1              14               5 2019-03-25 00:10:01  2019
2          1              14               5 2019-03-25 00:20:01  2019
3          1              14               5 2019-03-25 00:30:02  2019
4          1              14               5 2019-03-25 00:40:01  2019

#### Metric Derivation: Sum the Differences from the Last Time Step for Each Bike Station

https://stackoverflow.com/questions/53335567/use-pandas-shift-within-a-group
https://pandas.pydata.org/docs/reference/api/pandas.core.groupby.DataFrameGroupBy.shift.html

In [7]:
# Data needs to be sorted in a certain way for this to work (as above)
tenMinStationBikes = tenMinStationBikes.sort_values(['stationId','t'])

# Calculates the difference between number of bikes and those in the previous timestep if the same station

# prevAvailable bike will be filled with the value of availableBikes of the previous timestamp of the same station
tenMinStationBikes['prevAvailableBikes'] = tenMinStationBikes.groupby('stationId')['availableBikes'].shift(1) 

# always the first entry of a station will be nan; replace it with the value of availableBikes
tenMinStationBikes['prevAvailableBikes'].fillna(tenMinStationBikes['availableBikes'], inplace=True) 

# calculate the sum of activities by using the aboslute difference
tenMinStationBikes['activity'] = (tenMinStationBikes['prevAvailableBikes'] - tenMinStationBikes['availableBikes']).abs() 

In [8]:
tenMinStationBikes.head()

stationId  availableBikes  availableDocks                   t  year  \
0          1              14               5 2019-03-25 00:00:02  2019   
1          1              14               5 2019-03-25 00:10:01  2019   
2          1              14               5 2019-03-25 00:20:01  2019   
3          1              14               5 2019-03-25 00:30:02  2019   
4          1              14               5 2019-03-25 00:40:01  2019   

   prevAvailableBikes  activity  
0                14.0       0.0  
1                14.0       0.0  
2                14.0       0.0  
3                14.0       0.0  
4                14.0       0.0

#### Group the Data by Hour to See How Activity Changes Hourly

In [9]:
# import datetime
activityByHour = pd.DataFrame()

# group by day and hour, summing the activity
activityByHour['activity'] = tenMinStationBikes.groupby([tenMinStationBikes['t'].dt.year,tenMinStationBikes['t'].dt.weekday,tenMinStationBikes['t'].dt.hour])['activity'].sum()

In [10]:
# groupby puts the groups fields into a multilevel index, so we need to extract these and add as columns (and rename, because they are all originally given the name "t")
activityByHour.reset_index(level=2, inplace=True)
activityByHour.rename(columns={'t': 'hour'}, inplace=True)
activityByHour.reset_index(level=1, inplace=True)
activityByHour.rename(columns={'t': 'dayOfWeek'}, inplace=True)
activityByHour.reset_index(level=0, inplace=True)
activityByHour.rename(columns={'t': 'year'}, inplace=True)

In [11]:
# display
activityByHour.head()

year  dayOfWeek  hour  activity
0  2019          0     0     277.0
1  2019          0     1     237.0
2  2019          0     2      88.0
3  2019          0     3      84.0
4  2019          0     4     134.0

#### Plot Weekday Plots for Both 1-Week Periods

In [12]:
alt.Chart(activityByHour).mark_line().encode(
    x='hour:Q',
    y='activity:Q',
    color='year:N',
    column='dayOfWeek:Q',
).properties(
    width=100,
    height=100
)

alt.Chart(...)

##### Comments
Visuals reflect the same view that we have seen in the last 2 weeks of March visual which is plotted with the Dataset 1. There are less bike usage every day.

#### Group the Data by Day & by Location to See How Activity Changes by Location

In [13]:
# Make an empty data frame
activityByStation = pd.DataFrame()

# group by day and hour, summing the activity and add as a new column to the dataframe we just made
activityByStation['activity']=tenMinStationBikes.groupby([tenMinStationBikes['t'].dt.year,tenMinStationBikes['t'].dt.weekday,tenMinStationBikes['stationId']])['activity'].sum()

In [14]:
# groupby puts the groups fields into a multilevel index, so we need to extract these and add as columns (and rename, because they are all originally given the name "t")
activityByStation.reset_index(level=2, inplace=True)
activityByStation.reset_index(level=1, inplace=True)
activityByStation.rename(columns={'t': 'dayOfWeek'}, inplace=True)
activityByStation.reset_index(level=0, inplace=True)
activityByStation.rename(columns={'t': 'year'}, inplace=True)

In [15]:
# display
activityByStation.head()

year  dayOfWeek  stationId  activity
0  2019          0          1      46.0
1  2019          0          2      65.0
2  2019          0          3      82.0
3  2019          0          4      72.0
4  2019          0          5      89.0

##### StationID vs Location Name Matching

In [16]:
#Load the station names/location, and join them
stations=pd.read_csv('bikeStations.tsv', sep='\t')
stations["area"]=stations["name"].apply(lambda name: name.split(",")[1])

In [17]:
stations.head()

id                                  name        lat       lon  \
0   1            River Street , Clerkenwell  51.529163 -0.109971   
1   2        Phillimore Gardens, Kensington  51.499607 -0.197574   
2   3  Christopher Street, Liverpool Street  51.521284 -0.084606   
3   4       St. Chad's Street, King's Cross  51.530059 -0.120974   
4   5         Sedding Street, Sloane Square  51.493130 -0.156876   

                area  
0        Clerkenwell  
1         Kensington  
2   Liverpool Street  
3       King's Cross  
4      Sloane Square

##### Coordinate Transformation

In [18]:
transformer = Transformer.from_crs("epsg:4326", "EPSG:27700")
stations['x']=stations.apply(lambda row: transformer.transform(row['lat'],row['lon'])[0],axis=1)
stations['y']=stations.apply(lambda row: transformer.transform(row['lat'],row['lon'])[1],axis=1)
stations.head()

id                                  name        lat       lon  \
0   1            River Street , Clerkenwell  51.529163 -0.109971   
1   2        Phillimore Gardens, Kensington  51.499607 -0.197574   
2   3  Christopher Street, Liverpool Street  51.521284 -0.084606   
3   4       St. Chad's Street, King's Cross  51.530059 -0.120974   
4   5         Sedding Street, Sloane Square  51.493130 -0.156876   

                area              x              y  
0        Clerkenwell  531201.732340  182831.801961  
1         Kensington  525206.415593  179391.754240  
2   Liverpool Street  532984.001881  182001.341198  
3       King's Cross  530435.982367  182911.772902  
4      Sloane Square  528049.277060  178741.842635

In [19]:
stations.rename(columns = {'id':'stationId'}, inplace = True)

activityByStationMerged = activityByStation.merge(stations, how = 'left', on = 'stationId')

##### Plot the Maps to Show Activity in Stations by Day & Year

In [20]:
alt.data_transformers.disable_max_rows()
alt.Chart(activityByStationMerged).mark_circle().encode(
    # bin into half km squares
    alt.X('x', axis=alt.Axis(labels=False),scale=alt.Scale(zero=False)),
    alt.Y('y', axis=alt.Axis(labels=False),scale=alt.Scale(zero=False)),
    alt.Color('sum(activity)',scale=alt.Scale(scheme='purples',domain=[0,400])),
    column='dayOfWeek:Q',
    row='year:Q',
    tooltip=['area','sum(activity)']
).properties(
    width=100,
    height=100
)

alt.Chart(...)

Draw the same plot, but to prevent overlapping aggregate this dense spatial data into grid cells, by changing the x and y encoding.

In [21]:
alt.data_transformers.disable_max_rows()
alt.Chart(activityByStationMerged).mark_circle().encode(
    #bin into half km squares
    alt.X('x', bin=alt.Bin(step=500,nice=True), axis=alt.Axis(labels=False)),
    alt.Y('y', bin=alt.Bin(step=500,nice=True), axis=alt.Axis(labels=False)),
    alt.Color('sum(activity)',scale=alt.Scale(scheme='purples',domain=[0,400])),
    column='dayOfWeek:Q',
    row='year:Q',
    tooltip=['area','sum(activity)']
).properties(
    width=100,
    height=100
)

alt.Chart(...)

#### Comparison

Try to calculate and map the difference between 2020 and 2019.

Since fewer bike were used in 2020 than 2019, almost all places have seen a drop in usage. Try and calculate comparison measurement that account for this.

For example, what would you expect in 2020, assuming the spatial pattern was the same as in 2019 but with the reduced number of bikes we saw in 2020. Plotting the difference from what we "expect" tells us how things vary from our "expectation".